# Gaussian Equivalence

For jointly Gaussian $(X,Y)$: MMSE = LMMSE

## Setup and Imports

In [ ]:
import numpy as np
import matplotlib.pyplot as plt
from scipy import stats
import ipywidgets as widgets
from IPython.display import display
import seaborn as sns
from mpl_toolkits.mplot3d import Axes3D

# Set styling
plt.style.use('seaborn-v0_8')
sns.set_palette("husl")
%matplotlib inline
%config InlineBackend.figure_format = 'retina'

# Random seed for reproducibility
np.random.seed(42)

## Gaussian MMSE Theory

For jointly Gaussian $(X, Y)$ with parameters $(\mu_X, \mu_Y, \sigma_X^2, \sigma_Y^2, \rho)$:

$$\mathbb{E}[X|Y=y] = \mu_X + \rho\frac{\sigma_X}{\sigma_Y}(y - \mu_Y)$$

This is linear in $y$. Therefore MMSE = LMMSE for Gaussian case. Non-Gaussian: MMSE generally nonlinear.

In [ ]:
class GaussianEstimation:
    """
    Compare MMSE and LMMSE for Gaussian and non-Gaussian cases.
    
    Demonstrates that E[X|Y] is linear for jointly Gaussian,
    nonlinear otherwise.
    """
    
    def __init__(self, mu_x=0, mu_y=0, sigma_x=1, sigma_y=1, rho=0.7):
        self.mu_x = mu_x
        self.mu_y = mu_y
        self.sigma_x = sigma_x
        self.sigma_y = sigma_y
        self.rho = rho
        
        # Covariance matrix
        self.cov = np.array([
            [sigma_x**2, rho*sigma_x*sigma_y],
            [rho*sigma_x*sigma_y, sigma_y**2]
        ])
        
    def generate_gaussian_samples(self, n=1000):
        """Generate jointly Gaussian samples"""
        mean = [self.mu_x, self.mu_y]
        samples = np.random.multivariate_normal(mean, self.cov, n)
        return samples[:, 0], samples[:, 1]
    
    def generate_nongaussian_samples(self, n=1000, transform='quadratic'):
        """Generate non-Gaussian samples via transformation"""
        # Start with Gaussian
        x, y = self.generate_gaussian_samples(n)
        
        if transform == 'quadratic':
            # Apply nonlinear transform to X
            x = np.sign(x) * np.sqrt(np.abs(x))
        elif transform == 'exponential':
            # Transform to exponential marginals
            x = -np.log(1 - stats.norm.cdf(x)) / 1.5
            y = -np.log(1 - stats.norm.cdf(y)) / 1.5
        elif transform == 'mixture':
            # Create mixture by selective transformation
            mask = np.random.rand(n) > 0.5
            x[mask] = x[mask]**2 * np.sign(x[mask])
            
        return x, y
    
    def theoretical_mmse_gaussian(self, y):
        """Theoretical MMSE for Gaussian case"""
        return self.mu_x + self.rho * (self.sigma_x/self.sigma_y) * (y - self.mu_y)
    
    def empirical_mmse(self, x_samples, y_samples, y_test):
        """Empirical MMSE using kernel density estimation"""
        y_test = np.atleast_1d(y_test)
        result = np.zeros_like(y_test)
        
        for i, y_val in enumerate(y_test):
            # Kernel weights
            bandwidth = 0.3 * self.sigma_y
            weights = np.exp(-(y_samples - y_val)**2 / (2 * bandwidth**2))
            
            if weights.sum() > 1e-10:
                weights /= weights.sum()
                result[i] = np.sum(weights * x_samples)
            else:
                result[i] = self.mu_x
                
        return result
    
    def compute_lmmse(self, x_samples, y_samples):
        """Compute LMMSE coefficients from samples"""
        cov_xy = np.cov(x_samples, y_samples)[0, 1]
        var_y = np.var(y_samples)
        
        if var_y < 1e-10:
            a = 0
            b = np.mean(x_samples)
        else:
            a = cov_xy / var_y
            b = np.mean(x_samples) - a * np.mean(y_samples)
            
        return a, b

## Verification: Gaussian Case

Generate jointly Gaussian data. Compute MMSE via conditional density. Compute LMMSE via covariance. Show they are identical.

Key result: $\mathbb{E}[X|Y] = \mu_X + \frac{\text{Cov}(X,Y)}{\text{Var}(Y)}(Y - \mu_Y)$ exactly.

In [ ]:
def gaussian_equivalence_proof():
    """
    Prove MMSE = LMMSE for Gaussian case.
    """
    # Test parameters
    estimator = GaussianEstimation(mu_x=1, mu_y=-0.5, 
                                  sigma_x=1.5, sigma_y=2.0, 
                                  rho=0.75)
    
    # Generate samples
    n_samples = 2000
    x_gauss, y_gauss = estimator.generate_gaussian_samples(n_samples)
    
    # Test points
    y_test = np.linspace(y_gauss.min(), y_gauss.max(), 100)
    
    # 1. Theoretical MMSE (from Gaussian theory)
    mmse_theoretical = estimator.theoretical_mmse_gaussian(y_test)
    
    # 2. Empirical MMSE (kernel density)
    mmse_empirical = estimator.empirical_mmse(x_gauss, y_gauss, y_test)
    
    # 3. LMMSE (from covariance)
    a_lmmse, b_lmmse = estimator.compute_lmmse(x_gauss, y_gauss)
    lmmse_curve = a_lmmse * y_test + b_lmmse
    
    # Visualization
    fig, axes = plt.subplots(2, 3, figsize=(15, 10))
    
    # Joint distribution
    ax = axes[0, 0]
    ax.scatter(y_gauss, x_gauss, alpha=0.3, s=10)
    ax.set_xlabel('Y')
    ax.set_ylabel('X')
    ax.set_title('Jointly Gaussian Data')
    ax.grid(True, alpha=0.3)
    
    # Add correlation info
    correlation = np.corrcoef(x_gauss, y_gauss)[0, 1]
    ax.text(0.05, 0.95, f'ρ = {correlation:.3f}', transform=ax.transAxes,
           fontsize=12, va='top', bbox=dict(boxstyle='round', facecolor='yellow'))
    
    # MMSE curves comparison
    ax = axes[0, 1]
    ax.scatter(y_gauss[:500], x_gauss[:500], alpha=0.2, s=5, color='gray')
    ax.plot(y_test, mmse_theoretical, 'r-', linewidth=3, label='Theoretical MMSE')
    ax.plot(y_test, mmse_empirical, 'b--', linewidth=2, label='Empirical MMSE', alpha=0.8)
    ax.plot(y_test, lmmse_curve, 'g:', linewidth=2.5, label='LMMSE')
    ax.set_xlabel('Y')
    ax.set_ylabel('E[X|Y]')
    ax.set_title('MMSE vs LMMSE: All Identical!')
    ax.legend()
    ax.grid(True, alpha=0.3)
    
    # Difference plot
    ax = axes[0, 2]
    diff_theoretical_lmmse = mmse_theoretical - lmmse_curve
    diff_empirical_lmmse = mmse_empirical - lmmse_curve
    
    ax.plot(y_test, diff_theoretical_lmmse, 'r-', linewidth=2, 
           label='Theoretical - LMMSE')
    ax.plot(y_test, diff_empirical_lmmse, 'b--', linewidth=2, 
           label='Empirical - LMMSE')
    ax.axhline(0, color='black', linestyle='-', linewidth=0.5)
    ax.set_xlabel('Y')
    ax.set_ylabel('Difference')
    ax.set_title('Verification: Differences ≈ 0')
    ax.legend()
    ax.grid(True, alpha=0.3)
    ax.set_ylim([-0.1, 0.1])
    
    # Conditional density visualization
    ax = axes[1, 0]
    
    # Select specific Y values to condition on
    y_conditions = [-2, 0, 2]
    colors = ['blue', 'green', 'red']
    
    x_range = np.linspace(x_gauss.min(), x_gauss.max(), 100)
    
    for y_cond, color in zip(y_conditions, colors):
        # Theoretical conditional distribution p(x|y)
        # For Gaussian: X|Y=y ~ N(E[X|Y=y], Var(X|Y))
        mean_cond = estimator.theoretical_mmse_gaussian(y_cond)
        var_cond = estimator.sigma_x**2 * (1 - estimator.rho**2)
        
        pdf_cond = stats.norm.pdf(x_range, mean_cond, np.sqrt(var_cond))
        ax.plot(x_range, pdf_cond, color=color, linewidth=2, 
               label=f'p(X|Y={y_cond:.1f})')
        ax.axvline(mean_cond, color=color, linestyle='--', alpha=0.5)
    
    ax.set_xlabel('X')
    ax.set_ylabel('Density')
    ax.set_title('Conditional Densities (Gaussian)')
    ax.legend()
    ax.grid(True, alpha=0.3)
    
    # MSE comparison
    ax = axes[1, 1]
    
    # Compute MSE for different estimators
    mmse_pred_theoretical = estimator.theoretical_mmse_gaussian(y_gauss)
    mmse_pred_empirical = estimator.empirical_mmse(x_gauss, y_gauss, y_gauss)
    lmmse_pred = a_lmmse * y_gauss + b_lmmse
    
    mse_theoretical = np.mean((x_gauss - mmse_pred_theoretical)**2)
    mse_empirical = np.mean((x_gauss - mmse_pred_empirical)**2)
    mse_lmmse = np.mean((x_gauss - lmmse_pred)**2)
    
    bars = ax.bar(['Theoretical\nMMSE', 'Empirical\nMMSE', 'LMMSE'],
                  [mse_theoretical, mse_empirical, mse_lmmse],
                  color=['red', 'blue', 'green'], alpha=0.7)
    ax.set_ylabel('MSE')
    ax.set_title('MSE Comparison (Should be Equal)')
    ax.grid(True, alpha=0.3, axis='y')
    
    for bar, val in zip(bars, [mse_theoretical, mse_empirical, mse_lmmse]):
        ax.text(bar.get_x() + bar.get_width()/2, val*1.05,
               f'{val:.6f}', ha='center', fontsize=10)
    
    # Residual analysis
    ax = axes[1, 2]
    residuals = x_gauss - lmmse_pred
    ax.scatter(y_gauss, residuals, alpha=0.3, s=10)
    ax.axhline(0, color='red', linestyle='-', linewidth=1)
    ax.set_xlabel('Y')
    ax.set_ylabel('Residual (X - E[X|Y])')
    ax.set_title('Residuals: Zero Mean, Uncorrelated with Y')
    ax.grid(True, alpha=0.3)
    
    # Add correlation of residuals with Y
    residual_corr = np.corrcoef(residuals, y_gauss)[0, 1]
    ax.text(0.05, 0.95, f'Corr(ε, Y) = {residual_corr:.4f}', 
           transform=ax.transAxes, fontsize=11, va='top',
           bbox=dict(boxstyle='round', facecolor='yellow'))
    
    plt.suptitle('Gaussian Case: MMSE = LMMSE (Perfect Equivalence)', fontsize=14)
    plt.tight_layout()
    plt.show()
    
    print("\n=== Gaussian Equivalence Verification ===")
    print(f"Theoretical LMMSE coefficients:")
    print(f"  a = ρ(σ_X/σ_Y) = {estimator.rho * estimator.sigma_x / estimator.sigma_y:.6f}")
    print(f"  b = μ_X - a*μ_Y = {estimator.mu_x - (estimator.rho * estimator.sigma_x / estimator.sigma_y) * estimator.mu_y:.6f}")
    print(f"\nEmpirical LMMSE coefficients:")
    print(f"  a = {a_lmmse:.6f}")
    print(f"  b = {b_lmmse:.6f}")
    print(f"\nMSE values (all should be equal):")
    print(f"  Theoretical MMSE: {mse_theoretical:.6f}")
    print(f"  Empirical MMSE:   {mse_empirical:.6f}")
    print(f"  LMMSE:           {mse_lmmse:.6f}")

gaussian_equivalence_proof()

## Non-Gaussian: MMSE ≠ LMMSE

Transform Gaussian to non-Gaussian via nonlinear mapping. MMSE becomes nonlinear. LMMSE remains best linear approximation.

Performance gap = MSE(LMMSE) - MSE(MMSE) measures departure from Gaussianity.

In [ ]:
def nongaussian_comparison():
    """
    Show MMSE ≠ LMMSE for non-Gaussian cases.
    """
    estimator = GaussianEstimation(rho=0.7)
    n_samples = 2000
    
    # Test three transformations
    transformations = ['quadratic', 'exponential', 'mixture']
    
    fig, axes = plt.subplots(3, len(transformations), figsize=(15, 12))
    
    results = {}
    
    for idx, transform in enumerate(transformations):
        # Generate non-Gaussian samples
        x_nongauss, y_nongauss = estimator.generate_nongaussian_samples(
            n_samples, transform=transform)
        
        # Compute estimators
        y_test = np.linspace(y_nongauss.min(), y_nongauss.max(), 100)
        
        # MMSE (empirical)
        mmse_curve = estimator.empirical_mmse(x_nongauss, y_nongauss, y_test)
        
        # LMMSE
        a_lmmse, b_lmmse = estimator.compute_lmmse(x_nongauss, y_nongauss)
        lmmse_curve = a_lmmse * y_test + b_lmmse
        
        # Joint distribution
        ax = axes[0, idx]
        ax.scatter(y_nongauss, x_nongauss, alpha=0.3, s=10)
        ax.set_xlabel('Y')
        ax.set_ylabel('X')
        ax.set_title(f'{transform.capitalize()} Transform')
        ax.grid(True, alpha=0.3)
        
        # MMSE vs LMMSE
        ax = axes[1, idx]
        ax.scatter(y_nongauss[:300], x_nongauss[:300], alpha=0.2, s=5, color='gray')
        ax.plot(y_test, mmse_curve, 'r-', linewidth=2.5, label='MMSE (nonlinear)')
        ax.plot(y_test, lmmse_curve, 'b--', linewidth=2, label='LMMSE (linear)')
        ax.set_xlabel('Y')
        ax.set_ylabel('E[X|Y]')
        ax.set_title('MMSE ≠ LMMSE')
        ax.legend()
        ax.grid(True, alpha=0.3)
        
        # Difference and performance
        ax = axes[2, idx]
        
        # Compute MSE
        mmse_pred = estimator.empirical_mmse(x_nongauss, y_nongauss, y_nongauss)
        lmmse_pred = a_lmmse * y_nongauss + b_lmmse
        
        mse_mmse = np.mean((x_nongauss - mmse_pred)**2)
        mse_lmmse = np.mean((x_nongauss - lmmse_pred)**2)
        
        # Bar plot of MSE
        bars = ax.bar(['MMSE', 'LMMSE'], [mse_mmse, mse_lmmse],
                      color=['red', 'blue'], alpha=0.7)
        ax.set_ylabel('MSE')
        ax.set_title(f'Gap: {(mse_lmmse - mse_mmse)/mse_lmmse * 100:.1f}%')
        ax.grid(True, alpha=0.3, axis='y')
        
        for bar, val in zip(bars, [mse_mmse, mse_lmmse]):
            ax.text(bar.get_x() + bar.get_width()/2, val*1.05,
                   f'{val:.4f}', ha='center', fontsize=10)
        
        results[transform] = {
            'mse_mmse': mse_mmse,
            'mse_lmmse': mse_lmmse,
            'gap': mse_lmmse - mse_mmse
        }
    
    plt.suptitle('Non-Gaussian Cases: MMSE ≠ LMMSE (Nonlinearity Required)', fontsize=14)
    plt.tight_layout()
    plt.show()
    
    print("\n=== Non-Gaussian Results ===")
    for transform, res in results.items():
        print(f"\n{transform.capitalize()} transformation:")
        print(f"  MMSE:  {res['mse_mmse']:.6f}")
        print(f"  LMMSE: {res['mse_lmmse']:.6f}")
        print(f"  Gap:   {res['gap']:.6f} ({res['gap']/res['mse_lmmse']*100:.2f}% improvement possible)")

nongaussian_comparison()

## Interactive Correlation Analysis

As $|\rho| \to 1$: MMSE approaches perfect prediction. As $\rho \to 0$: MMSE approaches prior mean.

For Gaussian: MMSE slope = $\rho\sigma_X/\sigma_Y$. Always linear regardless of correlation strength.

In [ ]:
def interactive_correlation_analysis():
    """
    Interactive demo of correlation effects on MMSE=LMMSE.
    """
    
    # Widget controls
    rho_slider = widgets.FloatSlider(
        value=0.7, min=-0.95, max=0.95, step=0.05,
        description='Correlation ρ:',
        style={'description_width': 'initial'}
    )
    
    sigma_ratio_slider = widgets.FloatSlider(
        value=1.0, min=0.5, max=2.0, step=0.1,
        description='σ_X/σ_Y:',
        style={'description_width': 'initial'}
    )
    
    n_samples_slider = widgets.IntSlider(
        value=1000, min=500, max=2000, step=250,
        description='# Samples:',
        style={'description_width': 'initial'}
    )
    
    gaussian_checkbox = widgets.Checkbox(
        value=True,
        description='Gaussian',
        style={'description_width': 'initial'}
    )
    
    def update_plot(rho, sigma_ratio, n_samples, is_gaussian):
        # Create estimator
        estimator = GaussianEstimation(
            mu_x=0, mu_y=0,
            sigma_x=sigma_ratio, sigma_y=1.0,
            rho=rho
        )
        
        # Generate samples
        if is_gaussian:
            x_samples, y_samples = estimator.generate_gaussian_samples(n_samples)
        else:
            x_samples, y_samples = estimator.generate_nongaussian_samples(
                n_samples, transform='quadratic')
        
        # Compute estimators
        y_test = np.linspace(-3, 3, 100)
        
        # Theoretical MMSE (Gaussian formula)
        mmse_theoretical = estimator.theoretical_mmse_gaussian(y_test)
        
        # Empirical MMSE
        mmse_empirical = estimator.empirical_mmse(x_samples, y_samples, y_test)
        
        # LMMSE
        a_lmmse, b_lmmse = estimator.compute_lmmse(x_samples, y_samples)
        lmmse_curve = a_lmmse * y_test + b_lmmse
        
        # Visualization
        fig = plt.figure(figsize=(15, 10))
        gs = fig.add_gridspec(3, 3, hspace=0.3, wspace=0.3)
        
        # Joint distribution
        ax = fig.add_subplot(gs[0:2, 0:2])
        h = ax.scatter(y_samples, x_samples, alpha=0.4, s=20, 
                      c=np.sqrt(x_samples**2 + y_samples**2), cmap='viridis')
        ax.set_xlabel('Y', fontsize=12)
        ax.set_ylabel('X', fontsize=12)
        ax.set_title(f"{'Gaussian' if is_gaussian else 'Non-Gaussian'} (ρ = {rho:.2f})")
        ax.grid(True, alpha=0.3)
        plt.colorbar(h, ax=ax)
        
        # Overlay estimators
        ax.plot(y_test, mmse_empirical, 'r-', linewidth=3, label='MMSE', alpha=0.8)
        ax.plot(y_test, lmmse_curve, 'b--', linewidth=2.5, label='LMMSE', alpha=0.8)
        if is_gaussian:
            ax.plot(y_test, mmse_theoretical, 'g:', linewidth=2, 
                   label='Theoretical', alpha=0.8)
        ax.legend(fontsize=11)
        ax.set_xlim([-3, 3])
        ax.set_ylim([-3*sigma_ratio, 3*sigma_ratio])
        
        # Marginal distributions
        ax = fig.add_subplot(gs[0, 2])
        ax.hist(x_samples, bins=30, density=True, alpha=0.7, 
               orientation='horizontal', color='blue')
        ax.set_xlabel('Density')
        ax.set_ylabel('X')
        ax.set_title('p(X)')
        ax.grid(True, alpha=0.3)
        
        ax = fig.add_subplot(gs[1, 2])
        ax.hist(y_samples, bins=30, density=True, alpha=0.7, 
               orientation='horizontal', color='green')
        ax.set_xlabel('Density')
        ax.set_ylabel('Y')
        ax.set_title('p(Y)')
        ax.grid(True, alpha=0.3)
        
        # Performance metrics
        ax = fig.add_subplot(gs[2, 0])
        
        # MSE computation
        mmse_pred = estimator.empirical_mmse(x_samples, y_samples, y_samples)
        lmmse_pred = a_lmmse * y_samples + b_lmmse
        
        mse_mmse = np.mean((x_samples - mmse_pred)**2)
        mse_lmmse = np.mean((x_samples - lmmse_pred)**2)
        
        bars = ax.bar(['MMSE', 'LMMSE'], [mse_mmse, mse_lmmse],
                      color=['red', 'blue'], alpha=0.7)
        ax.set_ylabel('MSE')
        ax.set_title('Performance')
        ax.grid(True, alpha=0.3, axis='y')
        
        for bar, val in zip(bars, [mse_mmse, mse_lmmse]):
            ax.text(bar.get_x() + bar.get_width()/2, val*1.05,
                   f'{val:.4f}', ha='center')
        
        # Theoretical vs empirical slope
        ax = fig.add_subplot(gs[2, 1])
        theoretical_slope = rho * sigma_ratio
        empirical_slope = a_lmmse
        
        bars = ax.bar(['Theoretical\nSlope', 'Empirical\nSlope'],
                      [theoretical_slope, empirical_slope],
                      color=['green', 'blue'], alpha=0.7)
        ax.set_ylabel('LMMSE Slope')
        ax.set_title('Slope Verification')
        ax.grid(True, alpha=0.3, axis='y')
        
        for bar, val in zip(bars, [theoretical_slope, empirical_slope]):
            ax.text(bar.get_x() + bar.get_width()/2, val*1.05 if val > 0 else val-0.1,
                   f'{val:.3f}', ha='center')
        
        # Information content
        ax = fig.add_subplot(gs[2, 2])
        
        # Mutual information approximation
        if abs(rho) < 0.999:
            mi_gaussian = -0.5 * np.log(1 - rho**2)
        else:
            mi_gaussian = 5  # Cap for visualization
            
        # R-squared
        r_squared = 1 - mse_lmmse / np.var(x_samples)
        
        ax.text(0.1, 0.9, 'Information Metrics:', fontsize=12, fontweight='bold',
               transform=ax.transAxes)
        ax.text(0.1, 0.7, f'ρ² = {rho**2:.3f}', fontsize=11, transform=ax.transAxes)
        ax.text(0.1, 0.5, f'R² = {r_squared:.3f}', fontsize=11, transform=ax.transAxes)
        if is_gaussian:
            ax.text(0.1, 0.3, f'I(X;Y) = {mi_gaussian:.3f} nats', 
                   fontsize=11, transform=ax.transAxes)
        ax.text(0.1, 0.1, f'Var(X|Y)/Var(X) = {1-rho**2:.3f}', 
               fontsize=11, transform=ax.transAxes)
        ax.axis('off')
        
        plt.suptitle(f"MMSE {'=' if is_gaussian else '≠'} LMMSE: Effect of Correlation",
                    fontsize=14)
        plt.show()
        
        # Print summary
        print(f"\n{'='*50}")
        print(f"Distribution: {'Gaussian' if is_gaussian else 'Non-Gaussian'}")
        print(f"Correlation ρ = {rho:.3f}")
        print(f"σ_X/σ_Y = {sigma_ratio:.3f}")
        print(f"Theoretical LMMSE slope = ρ(σ_X/σ_Y) = {theoretical_slope:.3f}")
        print(f"Empirical LMMSE slope = {empirical_slope:.3f}")
        print(f"MSE ratio (LMMSE/MMSE) = {mse_lmmse/mse_mmse:.3f}")
        if is_gaussian:
            print("✓ MMSE = LMMSE (Gaussian case)")
        else:
            print(f"✗ MMSE < LMMSE by {(mse_lmmse-mse_mmse)/mse_lmmse*100:.1f}%")
    
    # Create interactive widget
    interactive_plot = widgets.interactive(
        update_plot,
        rho=rho_slider,
        sigma_ratio=sigma_ratio_slider,
        n_samples=n_samples_slider,
        is_gaussian=gaussian_checkbox
    )
    
    display(interactive_plot)

# Run interactive demo
interactive_correlation_analysis()

## High-Dimensional Analysis

Vector case: $\mathbb{E}[\mathbf{X}|\mathbf{Y}] = \boldsymbol{\mu}_X + \mathbf{K}_{XY}\mathbf{K}_{YY}^{-1}(\mathbf{Y} - \boldsymbol{\mu}_Y)$

Gaussian: Exact. Non-Gaussian: Best linear predictor. Curse of dimensionality affects empirical MMSE estimation.

In [ ]:
def high_dimensional_analysis():
    """
    Demonstrate MMSE=LMMSE in higher dimensions.
    """
    dimensions = [2, 5, 10, 20]
    n_samples = 1000
    
    fig, axes = plt.subplots(2, len(dimensions), figsize=(16, 8))
    
    results = {}
    
    for idx, d in enumerate(dimensions):
        # Generate d-dimensional Gaussian data
        # Create covariance with decaying correlations
        cov = np.eye(2*d)
        for i in range(d):
            for j in range(d):
                cov[i, d+j] = 0.7 * np.exp(-abs(i-j)/2)
                cov[d+j, i] = cov[i, d+j]
        
        # Generate samples
        samples = np.random.multivariate_normal(np.zeros(2*d), cov, n_samples)
        X = samples[:, :d]
        Y = samples[:, d:]
        
        # Compute LMMSE
        K_XX = np.cov(X.T)
        K_YY = np.cov(Y.T)
        K_XY = np.cov(X.T, Y.T)[:d, d:]
        
        # LMMSE matrix
        A_lmmse = K_XY @ np.linalg.inv(K_YY + 1e-6*np.eye(d))
        
        # Predictions
        X_pred = Y @ A_lmmse.T + (np.mean(X, axis=0) - np.mean(Y, axis=0) @ A_lmmse.T)
        
        # MSE
        mse_lmmse = np.mean((X - X_pred)**2)
        
        # Visualization for first component
        ax = axes[0, idx]
        ax.scatter(Y[:, 0], X[:, 0], alpha=0.3, s=10)
        ax.set_xlabel('$Y_1$')
        ax.set_ylabel('$X_1$')
        ax.set_title(f'd = {d}')
        ax.grid(True, alpha=0.3)
        
        # Add regression line
        y1_range = np.linspace(Y[:, 0].min(), Y[:, 0].max(), 50)
        x1_pred_simple = A_lmmse[0, 0] * y1_range + \
                        (np.mean(X[:, 0]) - A_lmmse[0, 0] * np.mean(Y[:, 0]))
        ax.plot(y1_range, x1_pred_simple, 'r-', linewidth=2)
        
        # Eigenvalue spectrum of K_YY
        ax = axes[1, idx]
        eigenvals = np.linalg.eigvalsh(K_YY)
        ax.semilogy(range(1, d+1), sorted(eigenvals, reverse=True), 'b.-')
        ax.set_xlabel('Index')
        ax.set_ylabel('Eigenvalue')
        ax.set_title(f'Condition: {max(eigenvals)/min(eigenvals):.1f}')
        ax.grid(True, alpha=0.3)
        
        results[d] = {
            'mse': mse_lmmse,
            'condition': max(eigenvals)/min(eigenvals)
        }
    
    plt.suptitle('High-Dimensional Gaussian: MMSE = LMMSE Still Holds', fontsize=14)
    plt.tight_layout()
    plt.show()
    
    print("\n=== Dimensionality Effects ===")
    for d, res in results.items():
        print(f"d = {d:2d}: MSE = {res['mse']:.4f}, Condition = {res['condition']:.1f}")

high_dimensional_analysis()

## Summary

1. **Jointly Gaussian**: MMSE = LMMSE (exact equivalence)
2. **Linearity of E[X|Y]**: Unique to Gaussian case
3. **Non-Gaussian**: MMSE < LMMSE (strict inequality)
4. **High dimensions**: Equivalence holds but estimation harder